In [4]:
#!/usr/bin/env python # coding: utf-8 # In[207]: 
import pandas as pd 
import numpy as np 
import seaborn as sns 
import matplotlib as mat 
#import psycopg2 
import seaborn as sns; sns.set() 
import matplotlib.pyplot as plt 
import datetime 
import scipy.stats 
from statistics import mean 
import plotly.express as px 
import plotly.graph_objects as go 
from plotly.subplots import make_subplots 
import chart_studio 
import plotly.io as pio 
import chart_studio.tools as tls 
import chart_studio.plotly as py
pd.set_option("display.precision", 4)
username = input("please input plotly username")
apikey = input(" please input api key: ")
chart_studio.tools.set_credentials_file(username=str(username), api_key=str(apikey))

please input plotly usernamecongruency
 please input api key: 5Cll2zTuPnnDNpjeNSb2


In [86]:
def clean_spins_upc(df):
	#take in a dataframe, expand the number of columns into a temp
	#datafram
	temp = df["Item_UPC"].str.rsplit(" ", n=1, expand = True)
    #df["Item_cleaned"] = df.apply(lambda x: x.Item_UPC.lstrip(x.Brand.lower()), axis=1)
	#add columns  to main dataframe from Temp
	df.insert(0, "UPC", temp[1])
	df.insert(1, "Item", temp[0])

	#drop original combined column
	df.drop(columns= ["Item_UPC"], inplace=True)
	#SPINS data adds a leading zero to UPC and includes hypen. 
	#neither are needed for analysis.
	df["UPC"]= df["UPC"].apply(lambda x : x[1:] if x.startswith("0") else x)
	df["UPC"]=df["UPC"].apply(lambda x :x.replace('-', ''))
	col_names = df.columns
    #make all columns lower case to ease searching
	for cols in col_names:
	    df[cols] = df[cols].apply(lambda x: x.lower() if type(x) == str else x)
        

def item_cleanup_is_in(x):
        if x[0] not in x[3] and x[1] not in x[3]:
            return x[0] + " "+ x[1] + " "+ x[2]
        elif x[0] in x[3] and x[1] in x[3]:
            return x[2]
        elif x[0] in x[3] and x[1] not in x[3]:
            return x[1]  + " " +x[2] 
        
        
def clean_up_item(df):

    #split cells and expand to clean up brands with >1 name ie Garden Of Life into 2 columns
    temp = df["Item"].str.split(" ", n=3, expand = True)
    brand_temp = df["Brand"].str.split(" ", n = 1, expand = True)

    #drop first columns as these should match

    temp.drop(columns = [0], inplace = True)
    brand_temp.drop(columns = [0], inplace = True)

    #and rename columns to concatenate
    temp.rename(columns = {1:0, 2:1, 3:2}, inplace = True)
    brand_temp.rename(columns = {1:3}, inplace = True)

    #remove none type objects from dataframe introduced by pandas.DataFrame.str.split() method
    temp[0] = temp[0].apply(lambda s: ' ' if s is None else str(s))
    temp[1] = temp[1].apply(lambda s: ' ' if s is None else str(s))
    temp[2] = temp[2].apply(lambda s: ' ' if s is None else str(s))
    brand_temp[3] = brand_temp[3].apply(lambda s: ' ' if s is None else str(s))
    #combine brand_temp and  temp df into 1 dataframe
    frames = [temp,brand_temp]
    result = pd.concat(frames, axis=1, join='inner')


    #remove brand names from columns
    temp[2] = result.apply(lambda x: item_cleanup_is_in(x), axis = 1)
    df.drop(columns= ["Item"], inplace=True)
    df.insert(2, "Item", temp[2])

def sub_set_metrics_of_interest(df, metric_to_use = ['ARP']):
	return df.loc[df["Metric"].isin(metric_to_use)].reset_index()


def subset_for_boxplots(df):
    metric_to_use = ['ARP']
    df = df[df["Metric"].isin(metric_to_use)].reset_index()

    return df

def cl_box_plot(df):
    fig = px.box(df, x="Metric", y="amount", points="all", title = df["Item"][0])
    fig.add_trace(go.Scatter(x=['ARP'], y=[get_MSRP(df.loc[0,"UPC"]),get_MSRP(df.loc[0,"UPC"])], mode="lines", name="MSRP"))
    fig.show()
    
def competive_analysis_easy_melt(df):
	#return df.melt(id_vars=["UPC", "Item","Geography",'Brand', 'Subcategory'], var_name = "Metric" , value_name='amount')

	return df.melt(id_vars=["index",'UPC', "Item","Geography",'Brand', 'Subcategory'], var_name = "Metric" , value_name='amount')

def competition_skus(upc_list,df):
    '''Select SKUs from a list to subset main data frame, item ID can be either full UPC or catalog ID
    df = the dataframe you are subsetting
    
    upc_list : a list of upcs that will be used to subset the dataframe.
    
    '''
    #df = df[df["Brand"].str.contains(brand)]
    df = df[df["UPC"].isin(list(upc_list))].reset_index(drop = True)
    df.dropna(inplace = True)
    #add the lines below once MSRP is procurred and get_msrp is modified for all brnds, not just CL
    #df.loc[:, "ARP_percent_off_MSRP"] =  df.loc[:,"ARP"].apply(lambda x: (1-(x/get_MSRP(item_id)))*100)
    
#     df.loc[:,'bins'] = pd.cut(df['ARP_percent_off_MSRP'],bins=[0,5,10,15,20,25,30,35,40], 
#                               labels=["0-5% off",
#                                       "5-10%  off",
#                                       "10-15% off",
#                                       "15-20% off",
#                                       "20-25% off",
#                                       "25-30% off", 
#                                       "30-35% off",
#                                       "35-40% off"])
    return df

def box_plot(df):
    fig = px.box(df, x="Metric", y="amount", points="all", title = df["Brand"][0] + " " + df["Item"][0] )
    #fig.add_trace(go.Scatter(x=['ARP'], y=[get_MSRP(df.loc[0,"UPC"]),get_MSRP(df.loc[0,"UPC"])], mode="lines", name="MSRP"))
    fig.show()
def box_plot2(df,index = 0):
    fig = px.box(df, x="Item", y="ARP", points="all", title = sheetname_list[index] , color = "Brand", hover_name = "Geography")
    #fig.add_trace(go.Scatter(x=['ARP'], y=[get_MSRP(df.loc[0,"UPC"]),get_MSRP(df.loc[0,"UPC"])], mode="lines", name="MSRP"))
    fig.show()
    py.plot(fig, sheetname_list[i], auto_open=False)

    
def box_plot3(df,index = 0):
    fig = px.box(df, x="Item", y="Units", points="all", title = sheetname_list[index] , color = "Brand", hover_name = "Geography")
    #fig.add_trace(go.Scatter(x=['ARP'], y=[get_MSRP(df.loc[0,"UPC"]),get_MSRP(df.loc[0,"UPC"])], mode="lines", name="MSRP"))
    fig.show()
    py.plot(fig, sheetname_list[i], auto_open=False)

    
def stacked_plots(df,index,send_to_plotly = False, auto_open=False):
    fig = make_subplots(rows=2, cols=1, shared_xaxes=True, 
                        vertical_spacing=0.02)

    fig.append_trace(go.Box(
        x=df["Item"],
        y=df["Units"],
        boxpoints ="all",
         hovertext = df["Geography"],
         jitter =0.5,
         boxmean = True, 
         showlegend=False
    ), row=1, col=1)

    fig.append_trace(go.Box(
        x=df["Item"],
        y=df["ARP"],
        boxpoints ="all",
        hovertext = df["Geography"],
         jitter =0.5,
         boxmean = True, 
         showlegend=False
    ), row=2, col=1)



    fig.update_layout(height=900, width=1100, title_text= sheetname_list[index] + "Units Sold (top) and ARP spread(bottom)")
    fig.show()
    if send_to:
        py.plot(fig, filename = " Units sold and ARP  " + sheetname_list[i] , auto_open=auto_open)

def scatter_plot_brands(df, index = 0,send_to_plotly, auto_open=False ):
    fig = px.scatter(df, x = "ARP",
                    y= "Units",
                    color = "Brand",
                    hover_data= ["Item"],
                    hover_name = "Geography",
                    title = sheetname_list[index] + " Total Units Sold by ARP" )
    fig.show()
    py.plot(fig, filename = sheetname_list[i] + " scatterplot", auto_open=auto_open)
    
def competiotn_make_plots(a_df_list = []):
    a_df_list = list(a_df_list)

    
    if len(a_df_list) == 1:
        box_plot(a_df_list[0])
    

    else:
        fig = make_subplots(
            rows=1, cols=2,
            specs=[[{"type": "box"}, {"type": "pie"}]],
        )

        fig.add_trace(go.Box( x=a_df_list[0].Metric, 
                             y=a_df_list[0].amount, 
                             boxpoints ="all",
                             hovertext =a_df_list[0]["Geography"],
                             jitter =0.5,
                             boxmean = True, 
                             showlegend=False,
                           # hovertemplate = 'Geography: $%{geography}'
                            ), 
                      row=1, col=1)
        #adds a line to reprsentMSRP
        fig.add_trace(go.Scatter(x=['ARP'], y=[get_MSRP(df.loc[0,"UPC"]),get_MSRP(df.loc[0,"UPC"])],
                                 mode="lines", name="MSRP", line=dict(color="#000000") ))

        #generates pie chart from calculated proportion data
        fig.add_trace(go.Pie(values=a_df_list[1]["count"], labels =a_df_list[1]["bins"], showlegend=True,
                             title_text ="Proportion MSRP Discounts"),
                      row=1, col=2)
        # Update xaxis properties
        fig.update_xaxes(title_text="Distribution of ARP vs Base ARP", row=1, col=1)
        #fig.update(title_text="Proportion of ARP as percentage discount",  row=1, col=2)

        fig.update_yaxes(title_text="Dollars", row=1, col=1)
        #fig.update_yaxes(title_text="Proportion of ARP as percentage discount",  row=1, col=2)

        #label the plot
        fig.update_layout(title_text=a_df_list[0]["Item"][0], height=600)
        fig.update_layout(height=600, showlegend=True)

        fig.show()
        #pio.write_html(fig, file=df["Item"][0]+'.html', auto_open=True)


def competition_single_product_analysis(item_id ,df):
    '''
    item_id will be UPC, 
    df = data frame of interest
    '''
    
    
    single_sku_df = competition_skus(((item_id)),df)
    
    #once MSRP for all SKU's are procured, add this
    #pie_frame = get_discount_proportions(single_sku_df)

    melted_df = competive_analysis_easy_meltt(single_sku_df)



    subset_df_forplot = subset_for_boxplots(melted_df)

    competiotn_make_plots(a_df_list =[subset_df_forplot])#, pie_frame)#add pie frame once MSRP is procured
    boot_strap_sample.plot_bootstrap_mean(single_sku_df["ARP"].to_numpy())
    #boot_strap_sample.plot_bootstrap_median(single_sku_df["ARP"].to_numpy(), test_statistic=np.median) 

def competitive_analysis_df_list(path):
    '''Typically vendors provide an excel sheet of items they are interested in.
    This function returns a list of data frames that contain which SKUs, provided by vendor, we are analyzing
    prior to loading, the excel file has the vendor provided skus separated by into sheets based on the category of the supplement
    '''
    sheetname_list = (pd.ExcelFile(path).sheet_names)
    sheetname_list.remove('Comp-Brands')
    sheetname_list.remove('Sheet13')
    sheetname_list.remove('Competitive-Item')
    sheetname_list.remove('Sheet1')

    df_list = []

    for sheet in sheetname_list:
        df = pd.read_excel(path, sheet_name = sheet, index_col=None, header = 0, usecols= ["UPC"])
        df["UPC"] = df["UPC"].astype(str)
        df["UPC"] = df["UPC"].apply(lambda x : x[1:] if x.startswith("0") else x)
        df["UPC"] = df["UPC"].apply(lambda x :x.replace('-', ''))
        df_list.append(df)
   # for df in df_list:
    
    return df_list,sheetname_list

def get_upc_list(df_list, index):
    '''returns a data frame which contains all geographic occurences of each sku of interest'''
    df2 = df_list[0]
    df2["UPC"]= df2["UPC"].apply(lambda x : x[1:] if x.startswith("0") else x)
    df2["UPC"]=df2["UPC"].apply(lambda x :x.replace('-', ''))
    upc_list = [upc for upc in df2["UPC"]]
    return df2,upc_list

In [47]:
#select the most up to date spins data, provide the file path to data,columns we want to investigate and na values 
path = "/Users/GuntherUlvanget/country_life/price_consult/SPINS_24_weeks_ending_7_12_20_for_competitive_analysis.csv"
cols = ['Geography', 'Item UPC','Brand','Subcategory','ARP','Units, Promo','Units, Non-Promo', "Units","Dollars"]
na_val = "-"
comp_analysis_df = pd.read_csv(path, sep = ",", na_values = na_val, usecols= cols)



comp_analysis_df.rename(columns =  {'Item UPC': 'Item_UPC', 'Units, Non-Promo':'Units_Non_Promo' }, inplace = True)

comp_analysis_df['ARP'] = comp_analysis_df['ARP'].astype(float)


clean_spins_upc(comp_analysis_df)
upc_list_path = "/Users/GuntherUlvanget/country_life/country_life_spins/Top Sellers_Competitive.xlsx"
df_list,sheetname_list = competitive_analysis_df_list(upc_list_path)

comp_analysis_df.head()
#empty dictionary for saving dataframes in. Name is related to sheetname list

UPC                                           Item  \
0  65801011832  garden life dr frm prob onc dly wmn ogc 30vcp   
1  85023200508         vital proteins collagen peptides 20 oz   
2  76899003790               nordic nat ultimate omega 180 sg   
3  85023200509         vital proteins collagen peptides 10 oz   
4  65801011664    garden life raw probtcs ultimte care 30 vcp   

                                         Geography            Brand  \
0                     earth fare - total us (corp)   garden of life   
1  sprouts farmers market - total us w/o pl (corp)   vital proteins   
2                     earth fare - total us (corp)  nordic naturals   
3  sprouts farmers market - total us w/o pl (corp)   vital proteins   
4                     earth fare - total us (corp)   garden of life   

                         Subcategory     Dollars    Units    ARP  \
0            prebiotics & probiotics  1.0579e+04    286.0  36.99   
1  protein & meal replacement powder  1.6506e+06  43469.0  37.97   
2                   supplements oils  3.2277e+04    544.0  59.33   
3  protein & meal replacement powder  9.6053e+05  41494.0  23.15   
4            prebiotics & probiotics  9.3582e+02     18.0  51.99   

   Units, Promo  Units_Non_Promo  
0           0.0            286.0  
1       27109.0          16360.0  
2          31.0            513.0  
3       20361.0          21133.0  
4           0.0             18.0

In [87]:
#d = {}
for i in range(len(sheetname_list)):
    df =competition_skus(df_list[i]["UPC"],comp_analysis_df  )
    stacked_plots(df, index = i)
    #box_plot3(df, index = i)
    scatter_plot_brands(df, index = i)
                    

In [80]:
items = list(df["UPC"].unique())

In [57]:
    summary_df = df.groupby ("Item", sort = False).agg({ "Dollars":"sum","Units":"sum","ARP":["min","max","mean", "median"]
                      ,"Units, Promo":["sum","max", "mean","median"]
                      ,"Units_Non_Promo": ["sum","max","mean","median"]
                      ,"Geography":"count"}).reset_index()

    sorted_summary = summary_df.sort_values([('Units','sum')], ascending=False).reset_index(drop = True)
    sorted_range =sorted_summary["ARP", "max"]-sorted_summary["ARP", "min"]
    sorted_summary.insert(3,"spread", sorted_range)
    d[sheetname_list[i]] = sorted_summary

In [92]:
d[sheetname_list[5]].corr()

Dollars   Units  spread     ARP                  \
                           sum     sum             min     max    mean   
Dollars         sum     1.0000  0.9319  0.2961  0.8952  0.8092  0.8076   
Units           sum     0.9319  1.0000  0.0765  0.6976  0.5868  0.5778   
spread                  0.2961  0.0765  1.0000  0.5714  0.7471  0.6959   
ARP             min     0.8952  0.6976  0.5714  1.0000  0.9724  0.9810   
                max     0.8092  0.5868  0.7471  0.9724  1.0000  0.9924   
                mean    0.8076  0.5778  0.6959  0.9810  0.9924  1.0000   
                median  0.7184  0.4732  0.7816  0.9309  0.9762  0.9821   
Units, Promo    sum     0.9509  0.9853  0.1211  0.7309  0.6264  0.6120   
                max     0.9305  0.9409  0.1421  0.7062  0.6124  0.5970   
                mean    0.9517  0.9777  0.1580  0.7421  0.6460  0.6328   
                median  0.7377  0.8146 -0.0640  0.5497  0.4270  0.4208   
Units_Non_Promo sum     0.8954  0.9899  0.0377  0.6544  0.5407  0.5365   
                max     0.8628  0.9561  0.0467  0.6190  0.5146  0.5143   
                mean    0.9004  0.9888  0.0479  0.6670  0.5539  0.5526   
                median  0.7629  0.9317 -0.1334  0.4355  0.3148  0.2919   
Geography       count   0.5700  0.6410 -0.1923  0.3954  0.2656  0.2504   

                               Units, Promo                          \
                        median          sum     max    mean  median   
Dollars         sum     0.7184       0.9509  0.9305  0.9517  0.7377   
Units           sum     0.4732       0.9853  0.9409  0.9777  0.8146   
spread                  0.7816       0.1211  0.1421  0.1580 -0.0640   
ARP             min     0.9309       0.7309  0.7062  0.7421  0.5497   
                max     0.9762       0.6264  0.6124  0.6460  0.4270   
                mean    0.9821       0.6120  0.5970  0.6328  0.4208   
                median  1.0000       0.5128  0.5162  0.5456  0.3020   
Units, Promo    sum     0.5128       1.0000  0.9760  0.9966  0.7957   
                max     0.5162       0.9760  1.0000  0.9844  0.6655   
                mean    0.5456       0.9966  0.9844  1.0000  0.7581   
                median  0.3020       0.7957  0.6655  0.7581  1.0000   
Units_Non_Promo sum     0.4297       0.9512  0.8908  0.9403  0.8122   
                max     0.4209       0.9136  0.8905  0.9142  0.6475   
                mean    0.4484       0.9502  0.8949  0.9421  0.7895   
                median  0.1825       0.9083  0.8403  0.8873  0.8724   
Geography       count   0.0785       0.5968  0.4590  0.5303  0.8004   

                       Units_Non_Promo                         Geography  
                                   sum     max    mean  median     count  
Dollars         sum             0.8954  0.8628  0.9004  0.7629    0.5700  
Units           sum             0.9899  0.9561  0.9888  0.9317    0.6410  
spread                          0.0377  0.0467  0.0479 -0.1334   -0.1923  
ARP             min             0.6544  0.6190  0.6670  0.4355    0.3954  
                max             0.5407  0.5146  0.5539  0.3148    0.2656  
                mean            0.5365  0.5143  0.5526  0.2919    0.2504  
                median          0.4297  0.4209  0.4484  0.1825    0.0785  
Units, Promo    sum             0.9512  0.9136  0.9502  0.9083    0.5968  
                max             0.8908  0.8905  0.8949  0.8403    0.4590  
                mean            0.9403  0.9142  0.9421  0.8873    0.5303  
                median          0.8122  0.6475  0.7895  0.8724    0.8004  
Units_Non_Promo sum             1.0000  0.9700  0.9989  0.9304    0.6634  
                max             0.9700  1.0000  0.9780  0.8562    0.5398  
                mean            0.9989  0.9780  1.0000  0.9158    0.6397  
                median          0.9304  0.8562  0.9158  1.0000    0.6784  
Geography       count           0.6634  0.5398  0.6397  0.6784    1.0000

In [55]:
    
with pd.ExcelWriter('/Users/GuntherUlvanget/Desktop/analysis3.xlsx') as writer:  
    d[sheetname_list[0]].to_excel(writer, sheet_name=sheetname_list[0])
    d[sheetname_list[1]].to_excel(writer, sheet_name=sheetname_list[1])
    d[sheetname_list[2]].to_excel(writer, sheet_name=sheetname_list[2])
    d[sheetname_list[3]].to_excel(writer, sheet_name=sheetname_list[3])
    d[sheetname_list[4]].to_excel(writer, sheet_name=sheetname_list[4])
    d[sheetname_list[5]].to_excel(writer, sheet_name=sheetname_list[5])
    d[sheetname_list[6]].to_excel(writer, sheet_name=sheetname_list[6])
    d[sheetname_list[7]].to_excel(writer, sheet_name=sheetname_list[7])
    d[sheetname_list[8]].to_excel(writer, sheet_name=sheetname_list[8])
    d[sheetname_list[9]].to_excel(writer, sheet_name=sheetname_list[9])
    d[sheetname_list[10]].to_excel(writer, sheet_name=sheetname_list[10])
    d[sheetname_list[11]].to_excel(writer, sheet_name=sheetname_list[11])
    

In [58]:
# def competitive_analysis_df_list(path):
#     '''Typically vendors provide an excel sheet of items they are interested in.
#     This function returns a list of data frames that contain which SKUs, provided by vendor, we are analyzing
#     prior to loading, the excel file has the vendor provided skus separated by into sheets based on the category of the supplement
#     '''
#     sheetname_list = (pd.ExcelFile(path).sheet_names)
#     sheetname_list.remove('Comp-Brands')
#     sheetname_list.remove('Sheet13')
#     sheetname_list.remove('Competitive-Item')
#     sheetname_list.remove('Sheet1')

#     df_list = []

#     for sheet in sheetname_list:
#         df = pd.read_excel(path, sheet_name = sheet, index_col=None, header = 0, usecols= ["UPC"])
#         df["UPC"] = df["UPC"].astype(str)
#         df["UPC"] = df["UPC"].apply(lambda x : x[1:] if x.startswith("0") else x)
#         df["UPC"] = df["UPC"].apply(lambda x :x.replace('-', ''))
#         df_list.append(df)
#    # for df in df_list:
    
#     return df_list

#clean_up_item(comp_analysis_df)

    




#upc_list = [upc for upc in df2["UPC"]]
 
#upc_list = [upc for upc in df["UPC"] for df in df_list]

#sheetname_list

#make this a function to iterate through list

# df2 = df_list[0]

# df2["UPC"]= df2["UPC"].apply(lambda x : x[1:] if x.startswith("0") else x)

# df2["UPC"]=df2["UPC"].apply(lambda x :x.replace('-', ''))

# upc_list = [upc for upc in df2["UPC"]]



#upc_list, comp_analysis_df = get_upc_list(df_list,3)



# melt_c_df = easy_melt(c_df)

# melt_c_df["Metric"].unique()

# df.melt(id_vars=['UPC', "Item","Geography", 'Subcategory'], var_name = "Metric" , value_name='amount')

# subset_for_boxplots(melt_c_df)



#  comp_analysis_df[comp_analysis_df["UPC"].isin(list(df_list[0]["UPC"]))].reset_index(drop = True)

# c_df = competition_skus(df_list[5]["UPC"],comp_analysis_df )



# for i in range(len(df_list)):
#     df =competition_skus(df_list[i]["UPC"],comp_analysis_df  )
#     box_plot2(df, index = i)
#     box_plot3(df, index = i)
#     scatter_plot_brands(df, index = i)
    

#for i in range(len(df_list)):
# df =competition_skus(df_list[i]["UPC"],comp_analysis_df  )
# summary_df = df.groupby ("Item", sort = False).agg({ "Units":"sum","ARP":["min","max","mean", "median"]
#                   ,"Units, Promo":["max", "mean","median"]
#                   ,"Units_Non_Promo": ["max","mean","median"]
#                   ,"Geography":"count"}).reset_index()


# sorted_summary = summary_df.sort_values([('Units','sum')], ascending=False).reset_index(drop = True)

# sorted_summary.to_excel(r'/Users/GuntherUlvanget/Desktop/' + sheetname_list[i]+'.xlsx', index_label = "Item")



# df.corr() 

# b =comp_analysis_df[comp_analysis_df["UPC"].isin(list(df_list[0]["UPC"]))]

# c = b.groupby("Item", sort = False).agg({"ARP":["min","max","mean", "median"]
#                       ,"Units, Promo":["max", "mean","median"]
#                       ,"Units_Non_Promo": ["max","mean","median"]
#                       ,"Geography":"count",
#                         "Units":"sum"}).reset_index()


# c.sort_values([('Units','sum')], ascending=False).reset_index(drop = True)

# #c_df.drop(columns =["index"], inplace = True)
# c_df.corr()

# c_df.drop(columns =["index"], inplace = True)



# def scatter_plot_brands(df, index):
#     fig = px.scatter(df, x = "ARP",
#                       y= "Units",
#                 color = "Brand",
#                     hover_name = "Geography",
#                     title = sheetname_list[index] + " Total Units Sold by ARP" )
#     fig.show()
    
# # ax1 =c_df.plot.scatter(x = "ARP",
# #                       y= "Units, Promo")
# scatter_plot_brands(c_df,index = 1)

# d = {}
# for i in range(len(sheetname_list)):
#     df =competition_skus(df_list[i]["UPC"],comp_analysis_df  )
#     box_plot2(df, index = i)
#     box_plot3(df, index = i)
#     scatter_plot_brands(df, index = i)

#     summary_df = df.groupby ("Item", sort = False).agg({ "Units":"sum","ARP":["min","max","mean", "median"]
#                       ,"Units, Promo":["max", "mean","median"]
#                       ,"Units_Non_Promo": ["max","mean","median"]
#                       ,"Geography":"count"}).reset_index()

#     sorted_summary = summary_df.sort_values([('Units','sum')], ascending=False).reset_index(drop = True)
#     sorted_range =sorted_summary["ARP", "max"]-sorted_summary["ARP", "min"]
#     sorted_summary.insert(2,"spread", sorted_range)
#     d[sheetname_list[i]] = sorted_summary

# sorted_summary.to_excel(r'/Users/GuntherUlvanget/Desktop/' + sheetname_list[i]+'.xlsx', index_label = "Item")



# df.cor

# sorted_range =sorted_summary["ARP", "max"]-sorted_summary["ARP", "min"]


# with pd.ExcelWriter('/Users/GuntherUlvanget/Desktop/analysis.xlsx') as writer:  
#     d[sheetname_list[0]].to_excel(writer, sheet_name=sheetname_list[0])
#     d[sheetname_list[1]].to_excel(writer, sheet_name=sheetname_list[1])
#     d[sheetname_list[2]].to_excel(writer, sheet_name=sheetname_list[2])
#     d[sheetname_list[3]].to_excel(writer, sheet_name=sheetname_list[3])
#     d[sheetname_list[4]].to_excel(writer, sheet_name=sheetname_list[4])
#     d[sheetname_list[5]].to_excel(writer, sheet_name=sheetname_list[5])
#     d[sheetname_list[6]].to_excel(writer, sheet_name=sheetname_list[6])
#     d[sheetname_list[7]].to_excel(writer, sheet_name=sheetname_list[7])
#     d[sheetname_list[8]].to_excel(writer, sheet_name=sheetname_list[8])
#     d[sheetname_list[9]].to_excel(writer, sheet_name=sheetname_list[9])
#     d[sheetname_list[10]].to_excel(writer, sheet_name=sheetname_list[10])
#     d[sheetname_list[11]].to_excel(writer, sheet_name=sheetname_list[11])
    


Dollars   Units  spread     ARP                  \
                           sum     sum             min     max    mean   
Dollars         sum     1.0000  0.8663  0.4488  0.1623  0.3110  0.2417   
Units           sum     0.8663  1.0000  0.2934 -0.2388 -0.0985 -0.1765   
spread                  0.4488  0.2934  1.0000  0.1405  0.4994  0.3671   
ARP             min     0.1623 -0.2388  0.1405  1.0000  0.9279  0.9675   
                max     0.3110 -0.0985  0.4994  0.9279  1.0000  0.9848   
                mean    0.2417 -0.1765  0.3671  0.9675  0.9848  1.0000   
                median  0.2125 -0.2075  0.3704  0.9565  0.9764  0.9965   
Units, Promo    sum     0.9239  0.9387  0.3665 -0.0351  0.1073  0.0259   
                max     0.9273  0.8704  0.4440  0.0806  0.2377  0.1621   
                mean    0.8773  0.9011  0.3251 -0.0095  0.1141  0.0442   
                median  0.6833  0.6898 -0.0152  0.1026  0.0841  0.0605   
Units_Non_Promo sum     0.7767  0.9765  0.2295 -0.3513 -0.2209 -0.2920   
                max     0.5018  0.7251  0.0695 -0.4848 -0.3981 -0.4411   
                mean    0.6652  0.9037  0.1208 -0.4323 -0.3328 -0.3872   
                median  0.6390  0.8459  0.1138 -0.1637 -0.1004 -0.1487   
Geography       count   0.7252  0.7743  0.4259 -0.1742  0.0080 -0.0931   

                               Units, Promo                          \
                        median          sum     max    mean  median   
Dollars         sum     0.2125       0.9239  0.9273  0.8773  0.6833   
Units           sum    -0.2075       0.9387  0.8704  0.9011  0.6898   
spread                  0.3704       0.3665  0.4440  0.3251 -0.0152   
ARP             min     0.9565      -0.0351  0.0806 -0.0095  0.1026   
                max     0.9764       0.1073  0.2377  0.1141  0.0841   
                mean    0.9965       0.0259  0.1621  0.0442  0.0605   
                median  1.0000      -0.0085  0.1357  0.0150  0.0309   
Units, Promo    sum    -0.0085       1.0000  0.9556  0.9746  0.7735   
                max     0.1357       0.9556  1.0000  0.9461  0.6627   
                mean    0.0150       0.9746  0.9461  1.0000  0.8119   
                median  0.0309       0.7735  0.6627  0.8119  1.0000   
Units_Non_Promo sum    -0.3190       0.8423  0.7633  0.7995  0.5948   
                max    -0.4523       0.5350  0.5128  0.5407  0.2591   
                mean   -0.4051       0.7369  0.6756  0.7425  0.5289   
                median -0.1752       0.7502  0.6789  0.7340  0.6801   
Geography       count  -0.1279       0.7323  0.6265  0.6083  0.4292   

                       Units_Non_Promo                         Geography  
                                   sum     max    mean  median     count  
Dollars         sum             0.7767  0.5018  0.6652  0.6390    0.7252  
Units           sum             0.9765  0.7251  0.9037  0.8459    0.7743  
spread                          0.2295  0.0695  0.1208  0.1138    0.4259  
ARP             min            -0.3513 -0.4848 -0.4323 -0.1637   -0.1742  
                max            -0.2209 -0.3981 -0.3328 -0.1004    0.0080  
                mean           -0.2920 -0.4411 -0.3872 -0.1487   -0.0931  
                median         -0.3190 -0.4523 -0.4051 -0.1752   -0.1279  
Units, Promo    sum             0.8423  0.5350  0.7369  0.7502    0.7323  
                max             0.7633  0.5128  0.6756  0.6789    0.6265  
                mean            0.7995  0.5407  0.7425  0.7340    0.6083  
                median          0.5948  0.2591  0.5289  0.6801    0.4292  
Units_Non_Promo sum             1.0000  0.7990  0.9521  0.8534    0.7526  
                max             0.7990  1.0000  0.8982  0.5066    0.4558  
                mean            0.9521  0.8982  1.0000  0.7701    0.5784  
                median          0.8534  0.5066  0.7701  1.0000    0.5590  
Geography       count           0.7526  0.4558  0.5784  0.5590    1.0000

In [50]:
# for i in range(len(sheetname_list)):
#     df =competition_skus(df_list[i]["UPC"],comp_analysis_df  )
#     df.hist(column = "ARP", by= "Geography")

In [44]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go
# def stacked_plots(df,index):
#     fig = make_subplots(rows=2, cols=1, shared_xaxes=True, 
#                         vertical_spacing=0.02)

#     fig.append_trace(go.Box(
#         x=df["Item"],
#         y=df["Units"],
#         boxpoints ="all",
#          hovertext = df["Geography"],
#          jitter =0.5,
#          boxmean = True, 
#          showlegend=False
#     ), row=1, col=1)

#     fig.append_trace(go.Box(
#         x=df["Item"],
#         y=df["ARP"],
#         boxpoints ="all",
#         hovertext = df["Geography"],
#          jitter =0.5,
#          boxmean = True, 
#          showlegend=False
#     ), row=2, col=1)



#     fig.update_layout(height=900, width=1100, title_text= sheetname_list[index] + "Units Sold (top) and ARP spread(bottom)")
#     fig.show()
#     py.plot(fig, filename = " Units sold and ARP  " + sheetname_list[i] , auto_open=False)


In [72]:
# d[sheetname_list[0]]

In [76]:
df[df["UPC"]=="07628039151"]

UPC                                     Item  \
0    07628039151  solaray magnesium glycnt 400 mg 120 vcp   
9    07628039151  solaray magnesium glycnt 400 mg 120 vcp   
18   07628039151  solaray magnesium glycnt 400 mg 120 vcp   
27   07628039151  solaray magnesium glycnt 400 mg 120 vcp   
36   07628039151  solaray magnesium glycnt 400 mg 120 vcp   
52   07628039151  solaray magnesium glycnt 400 mg 120 vcp   
60   07628039151  solaray magnesium glycnt 400 mg 120 vcp   
76   07628039151  solaray magnesium glycnt 400 mg 120 vcp   
85   07628039151  solaray magnesium glycnt 400 mg 120 vcp   
97   07628039151  solaray magnesium glycnt 400 mg 120 vcp   
112  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
127  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
136  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
151  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
163  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
178  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
192  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
205  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
218  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
230  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
244  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
259  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
272  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
287  07628039151  solaray magnesium glycnt 400 mg 120 vcp   
299  07628039151  solaray magnesium glycnt 400 mg 120 vcp   

                                             Geography    Brand  \
0                         earth fare - total us (corp)  solaray   
9                 earth fare - north central (rgn/mkt)  solaray   
18                    earth fare - southeast (rgn/mkt)  solaray   
27        fresh thyme farmers market - total us (corp)  solaray   
36                        greenacres - total us (corp)  solaray   
52             greens natural market - total us (corp)  solaray   
60                             infra - total us (corp)  solaray   
76             luckys farmers market - total us (corp)  solaray   
85             natural grocers by vc - total us (corp)  solaray   
97                               ncg - total us (corp)  solaray   
112                         ncg - total us x-pcc (ban)  solaray   
127                                    ncg - pcc (ban)  solaray   
136                       ncg - mid atlantic (rgn/mkt)  solaray   
151                      ncg - north central (rgn/mkt)  solaray   
163                         ncg - north east (rgn/mkt)  solaray   
178                         ncg - north west (rgn/mkt)  solaray   
192                    ncg - northwest x-pcc (rgn/mkt)  solaray   
205                      ncg - south central (rgn/mkt)  solaray   
218                         ncg - south east (rgn/mkt)  solaray   
230                         ncg - south west (rgn/mkt)  solaray   
244                           ncg - east rgn (rgn/mkt)  solaray   
259                        ncg - central rgn (rgn/mkt)  solaray   
272                         ncg - west x-pcc (rgn/mkt)  solaray   
287  new seasons markets + new leaf community marke...  solaray   
299    sprouts farmers market - total us w/o pl (corp)  solaray   

        Subcategory    Dollars    Units    ARP  Units, Promo  Units_Non_Promo  
0    minerals other    3526.32    168.0  20.99           0.0            168.0  
9    minerals other     356.83     17.0  20.99           0.0             17.0  
18   minerals other    3001.57    143.0  20.99           0.0            143.0  
27   minerals other   35031.40   2331.0  15.03        1127.0           1204.0  
36   minerals other    2049.87    147.0  13.94          42.0            105.0  
52   minerals other    1020.01     58.0  17.59          14.0             44.0  
60   minerals other   90759.01   5963.4  15.22        2208.7           3754.7  
76   minerals other     565.90     30.0  18

In [79]:
calculate_mean('02124581209',df)

26.13

In [77]:
import boot_strap_sample
import warnings
warnings.filterwarnings('ignore')
  
def Average(lst): 
    return mean(lst) 

def calculate_mean(upc,df):
    single_sku_df = df[df["UPC"]== upc]
    means, ci = boot_strap_sample.bootstrap_ci(single_sku_df["ARP"].to_numpy())
    return round(Average(means),2)

# means, ci = boot_strap_sample.bootstrap_ci(single_sku_df["ARP"].to_numpy())
# estimates = [calculate_mean(item) for item in items]




In [82]:
estimates = [calculate_mean(item,df) for item in items]

In [83]:
estimates

[16.06,
 26.11,
 15.15,
 15.31,
 10.37,
 10.52,
 8.59,
 15.24,
 8.61,
 15.05,
 32.01,
 8.6,
 11.46,
 24.09,
 19.21,
 21.94]

In [ ]:
# from plotly.subplots import make_subplots
# import plotly.graph_objects as go

# fig = make_subplots(
#     rows=2, cols=2,
#     specs=[[{"colspan": 2}, None], [{}, {}]],
#     subplot_titles=("ARP Subplot","Uits Subplot", "Units vs ARP Subplot"),
# vertical_spacing=0.5)

# fig.append_trace(go.Scatter(
#     x=df["ARP"],
#     y=df["Units"],
#     mode = "markers",
#     hovertext= df["Brand"]
# ), row=1, col=1)

# fig.append_trace(go.Box(
#     x=df["Item"],
#     y=df["ARP"],
#     boxpoints ="all",
#      hovertext = df["Geography"],
#      jitter =0.5,
#      boxmean = True, 
#      showlegend=False
# ), row=2, col=1)

# fig.append_trace(go.Box(
#     x=df["Item"],
#     y=df["Units"],
#     hovertext = df["Geography"],
#      jitter =0.5,
#      boxmean = True, 
#      showlegend=False
# ), row=2, col=2)



# #fig.update_layout(height=900, width=900, title_text="Stacked Subplots")
# fig.show()
